In [ ]:
# import torch
# import numpy as np
# import random
# from torch.distributions import Uniform, InverseGamma
# import matplotlib.pyplot as plt
# # Set the random seed
# seed = 7
# random.seed(seed)
# np.random.seed(seed)
# torch.manual_seed(seed)

# # Define distributions
# uniform_dist = Uniform(0.0, 1.0)
# inv_gamma_dist = InverseGamma(concentration=1.5, rate=0.6)  # PyTorch uses 'rate' instead of 'scale'

# # Sample data
# A = 2 * uniform_dist.sample((1000,))
# X = inv_gamma_dist.sample((1000,))
# R1 = A * X

# # Split into training and evaluation datasets
# train_dataset = R1[:250].reshape(250, 1)
# eval_dataset = R1[250:].reshape(750, 1)

# # Print maximum values
# print(torch.max(train_dataset))
# print(torch.max(eval_dataset))


tensor(51.3337)
tensor(26.1378)


In [1]:
# plt.hist(eval_dataset,bins=100,density=True)

In [ ]:
from herbie import Herbie
from datetime import datetime, timedelta
import os

# --- Configuration FOR SMALL TEST ---
years_to_download = [2019] # Test with only one year

# Override start and end dates for a very short test period
test_start_date_override = datetime(2019, 1, 1, 0) # Year, Month, Day, Hour (00Z on Jan 1st)
test_end_date_override = datetime(2019, 1, 1, 2)   # Year, Month, Day, Hour (02Z on Jan 1st)
                                                   # This will process 00Z, 01Z, and 02Z

forecast_hour = 1  # e.g., F01 for 1-hour forecast.

# Variable definitions: name, GRIB search string, HRRR product type
variables_to_download = {
    "VIL": {
        "search_string": ":VIL:entire atmosphere:",
        "product": "sfc"
    },
    "VGRD": {
        "search_string": ":VGRD:20 mb:",
        "product": "prs"
    }
}

output_base_dir = "./hrrr_test_data" # Use a separate directory for the test
os.makedirs(output_base_dir, exist_ok=True)
herbie_cache_dir = os.path.join(output_base_dir, "temp_herbie_cache")
# --- End Configuration ---

# --- Main Script (Keep the rest of the script as it was) ---
for year in years_to_download:
    print(f"\nProcessing Year: {year}")

    # Determine start and end dates for the current year
    # but override if test dates are set for this year
    current_year_start_date = datetime(year, 1, 1, 0)
    current_year_end_date = datetime(year, 12, 31, 23)

    if 'test_start_date_override' in locals() and year == test_start_date_override.year:
        current_year_start_date = test_start_date_override
        print(f"  >> Test Mode: Overriding start date to {current_year_start_date}")
    if 'test_end_date_override' in locals() and year == test_end_date_override.year:
        current_year_end_date = test_end_date_override
        print(f"  >> Test Mode: Overriding end date to {current_year_end_date}")


    current_date = current_year_start_date
    while current_date <= current_year_end_date:
        print(f"  Processing DateTime: {current_date.strftime('%Y-%m-%d %H:%M')} F{forecast_hour:02d}")

        for var_name, var_info in variables_to_download.items():
            print(f"    Attempting to download: {var_name} (Product: {var_info['product']}, Level: {'20mb' if var_name == 'VGRD' else 'N/A'})")
            try:
                H = Herbie(
                    current_date,
                    model="hrrr",
                    product=var_info['product'],
                    fxx=forecast_hour,
                    save_dir=herbie_cache_dir,
                    overwrite=False
                )

                downloaded_grib_paths = H.download(searchString=var_info['search_string'])

                if downloaded_grib_paths:
                    if isinstance(downloaded_grib_paths, str):
                        downloaded_grib_paths = [downloaded_grib_paths]

                    for downloaded_file_path in downloaded_grib_paths:
                        if os.path.exists(downloaded_file_path):
                            target_dir = os.path.join(output_base_dir, str(year), current_date.strftime('%Y%m%d'))
                            os.makedirs(target_dir, exist_ok=True)

                            level_suffix = ""
                            if var_name == "VGRD":
                                level_suffix = ".lev20mb"

                            final_filename = (f"hrrr.t{current_date.strftime('%H')}z."
                                              f"f{forecast_hour:02d}."
                                              f"{current_date.strftime('%Y%m%d')}."
                                              f"{var_name.lower()}{level_suffix}.grib2")
                            final_path = os.path.join(target_dir, final_filename)

                            if os.path.exists(final_path):
                                print(f"      INFO: Target file {final_path} already exists. Skipping move.")
                            else:
                                os.rename(downloaded_file_path, final_path)
                                print(f"      Successfully downloaded and saved: {final_path}")
                        else:
                            print(f"      WARNING: Herbie reported download but file not found: {downloaded_file_path}")
                else:
                    print(f"      INFO: No {var_name} data found or downloaded for "
                          f"{current_date.strftime('%Y-%m-%d %H:%M')} F{forecast_hour:02d} "
                          f"with product '{var_info['product']}' matching '{var_info['search_string']}'.")

            except Exception as e:
                print(f"      ERROR processing {var_name} for {current_date}: {e}")

        current_date += timedelta(hours=1)

print("\nDownload process finished.")
print(f"Data saved in: {output_base_dir}")
print(f"Herbie cache was at: {herbie_cache_dir} (you may want to inspect/clean it)")


Processing Year: 2019
  >> Test Mode: Overriding start date to 2019-01-01 00:00:00
  >> Test Mode: Overriding end date to 2019-01-01 02:00:00
  Processing DateTime: 2019-01-01 00:00 F01
    Attempting to download: VIL (Product: sfc, Level: N/A)
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2019-Jan-01 00:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


C:\Users\adity\AppData\Local\Temp\ipykernel_21060\608697508.py:65: DeprecationWarning: The argument `searchString` was renamed `search`. Please update your scripts.
  downloaded_grib_paths = H.download(searchString=var_info['search_string'])


👨🏻‍🏭 Created directory: [hrrr_test_data\temp_herbie_cache\hrrr\20190101]
      ERROR processing VIL for 2019-01-01 00:00:00: 'WindowsPath' object is not iterable
    Attempting to download: VGRD (Product: prs, Level: 20mb)
✅ Found ┊ model=hrrr ┊ product=prs ┊ 2019-Jan-01 00:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


C:\Users\adity\AppData\Local\Temp\ipykernel_21060\608697508.py:65: DeprecationWarning: The argument `searchString` was renamed `search`. Please update your scripts.
  downloaded_grib_paths = H.download(searchString=var_info['search_string'])
🦨 No subsets found with search=':VGRD:20 mb:' in self.model='hrrr' self.date=Timestamp('2019-01-01 00:00:00') self.fxx=1


      ERROR processing VGRD for 2019-01-01 00:00:00: 'WindowsPath' object is not iterable
  Processing DateTime: 2019-01-01 01:00 F01
    Attempting to download: VIL (Product: sfc, Level: N/A)
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2019-Jan-01 01:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


...

      ERROR processing VGRD for 2019-01-01 01:00:00: 'WindowsPath' object is not iterable
  Processing DateTime: 2019-01-01 02:00 F01
    Attempting to download: VIL (Product: sfc, Level: N/A)
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2019-Jan-01 02:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


C:\Users\adity\AppData\Local\Temp\ipykernel_21060\608697508.py:65: DeprecationWarning: The argument `searchString` was renamed `search`. Please update your scripts.
  downloaded_grib_paths = H.download(searchString=var_info['search_string'])


      ERROR processing VIL for 2019-01-01 02:00:00: 'WindowsPath' object is not iterable
    Attempting to download: VGRD (Product: prs, Level: 20mb)
✅ Found ┊ model=hrrr ┊ product=prs ┊ 2019-Jan-01 02:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


C:\Users\adity\AppData\Local\Temp\ipykernel_21060\608697508.py:65: DeprecationWarning: The argument `searchString` was renamed `search`. Please update your scripts.
  downloaded_grib_paths = H.download(searchString=var_info['search_string'])
🦨 No subsets found with search=':VGRD:20 mb:' in self.model='hrrr' self.date=Timestamp('2019-01-01 02:00:00') self.fxx=1


      ERROR processing VGRD for 2019-01-01 02:00:00: 'WindowsPath' object is not iterable

Download process finished.
Data saved in: ./hrrr_test_data
Herbie cache was at: ./hrrr_test_data\temp_herbie_cache (you may want to inspect/clean it)


In [4]:
date=datetime(2019, 1, 1, 0)
H = Herbie(date, model='hrrr', product='prs', fxx=1)
print(H.inventory())

✅ Found ┊ model=hrrr ┊ product=prs ┊ 2019-Jan-01 00:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws
     grib_message  start_byte     end_byte                range  \
0               1           0     771236.0             0-771236   
1               2      771237    1339079.0       771237-1339079   
2               3     1339080    1787645.0      1339080-1787645   
3               4     1787646    1787833.0      1787646-1787833   
4               5     1787834    2792662.0      1787834-2792662   
..            ...         ...          ...                  ...   
693           694   378908595  378926294.0  378908595-378926294   
694           695   378926295  380470808.0  378926295-380470808   
695           696   380470809  382008866.0  380470809-382008866   
696           697   382008867  383425313.0  382008867-383425313   
697           698   383425314          NaN           383425314-   

    reference_time          valid_time variable              level  \
0       2019-01-01 2019-01-01 01:00:

In [25]:
from herbie import Herbie

H = Herbie("2019-01-01 00:00", model="hrrr", product="prs", fxx=1)
inv = H.inventory()

# Check for all available variable names
inv.head(20)
# print(list(inv['variable']))
# print(inv['name'].unique())

# # Check for VVEL
# vvel_df = inv[inv['name'] == 'VVEL']
# print(vvel_df)

✅ Found ┊ model=hrrr ┊ product=prs ┊ 2019-Jan-01 00:00 UTC F01 ┊ GRIB2 @ aws ┊ IDX @ aws


grib_message  start_byte   end_byte            range reference_time  \
0              1           0   771236.0         0-771236     2019-01-01   
1              2      771237  1339079.0   771237-1339079     2019-01-01   
2              3     1339080  1787645.0  1339080-1787645     2019-01-01   
3              4     1787646  1787833.0  1787646-1787833     2019-01-01   
4              5     1787834  2792662.0  1787834-2792662     2019-01-01   
5              6     2792663  3113597.0  2792663-3113597     2019-01-01   
6              7     3113598  3711887.0  3113598-3711887     2019-01-01   
7              8     3711888  4281949.0  3711888-4281949     2019-01-01   
8              9     4281950  4884785.0  4281950-4884785     2019-01-01   
9             10     4884786  4884973.0  4884786-4884973     2019-01-01   
10            11     4884974  4885161.0  4884974-4885161     2019-01-01   
11            12     4885162  4885349.0  4885162-4885349     2019-01-01   
12            13     4885350  4885537.0  4885350-4885537     2019-01-01   
13            14     4885538  4885725.0  4885538-4885725     2019-01-01   
14            15     4885726  5661473.0  4885726-5661473     2019-01-01   
15            16     5661474  6233374.0  5661474-6233374     2019-01-01   
16            17     6233375  6682942.0  6233375-6682942     2019-01-01   
17            18     6682943  6683130.0  6682943-6683130     2019-01-01   
18            19     6683131  7505346.0  6683131-7505346     2019-01-01   
19            20     7505347  7927124.0  7505347-7927124     2019-01-01   

            valid_time variable  level forecast_time  \
0  2019-01-01 01:00:00      HGT  50 mb   1 hour fcst   
1  2019-01-01 01:00:00      TMP  50 mb   1 hour fcst   
2  2019-01-01 01:00:00       RH  50 mb   1 hour fcst   
3  2019-01-01 01:00:00      DPT  50 mb   1 hour fcst   
4  2019-01-01 01:00:00     SPFH  50 mb   1 hour fcst   
5  2019-01-01 01:00:00     VVEL  50 mb   1 hour fcst   
6  2019-01-01 01:00:00     UGRD  50 mb   1 hour fcst   
7  2019-01-01 01:00:00     VGRD  50 mb   1 hour fcst   
8  2019-01-01 01:00:00     ABSV  50 mb   1 hour fcst   
9  2019-01-01 01:00:00     CLMR  50 mb   1 hour fcst   
10 2019-01-01 01:00:00   CIMIXR  50 mb   1 hour fcst   
11 2019-01-01 01:00:00     RWMR  50 mb   1 hour fcst   
12 2019-01-01 01:00:00     SNMR  50 mb   1 hour fcst   
13 2019-01-01 01:00:00     GRLE  50 mb   1 hour fcst   
14 2019-01-01 01:00:00      HGT  75 mb   1 hour fcst   
15 2019-01-01 01:00:00      TMP  75 mb   1 hour fcst   
16 2019-01-01 01:00:00       RH  75 mb   1 hour fcst   
17 2019-01-01 01:00:00      DPT  75 mb   1 hour fcst   
18 2019-01-01 01:00:00     SPFH  75 mb   1 hour fcst   
19 2019-01-01 01:00:00     VVEL  75 mb   1 hour fcst   

                  search_this  
0      :HGT:50 mb:1 hour fcst  
1      :TMP:50 mb:1 hour fcst  
2       :RH:50 mb:1 hour fcst  
3      :DPT:50 mb:1 hour fcst  
4     :SPFH:50 mb:1 hour fcst  
5     :VVEL:50 mb:1 hour fcst  
6     :UGRD:50 mb:1 hour fcst  
7     :VGRD:50 mb:1 hour fcst  
8     :ABSV:50 mb:1 hour fcst  
9     :CLMR:50 mb:1 hour fcst  
10  :CIMIXR:50 mb:1 hour fcst  
11    :RWMR:50 mb:1 hour fcst  
12    :SNMR:50 mb:1 hour fcst  
13    :GRLE:50 mb:1 hour fcst  
14     :HGT:75 mb:1 hour fcst  
15     :TMP:75 mb:1 hour fcst  
16      :RH:75 mb:1 hour fcst  
17     :DPT:75 mb:1 hour fcst  
18    :SPFH:75 mb:1 hour fcst  
19    :VVEL:75 mb:1 hour fcst

In [31]:
pwd

'c:\\Users\\adity\\OneDrive\\Desktop\\mscThesis\\Code3\\Thesis_FLow'

In [ ]:
from herbie import Herbie
import pandas as pd

# Define date range for first week of Jan 2019, hourly
dates = pd.date_range("2020-01-01", "2021-12-31", freq="1H")

for date in dates:
    print(f"⏳ Processing: {date}")
    
    # --- Download VIL from HRRR (surface product)
    try:
        H_hrrr = Herbie(date, model="hrrr", product="sfc", fxx=0,save_dir="c:\\Users\\adity\\OneDrive\\Desktop\\mscThesis\\Code3\\Thesis_FLow\\bigdata")
        H_hrrr.download(search=':VIL:')
        print("✅ Downloaded VIL")
    except Exception as e:
        print(f"❌ Failed VIL at {date}: {e}")
    
    # --- Download VVEL at 20 mb from GFS (pressure-level product)
    try:
        H_gfs = Herbie(date, model="hrrr", product="prs", fxx=0,save_dir="c:\\Users\\adity\\OneDrive\\Desktop\\mscThesis\\Code3\\Thesis_FLow\\bigdata")
        H_gfs.download(search=':VVEL:75 mb:')
        print("✅ Downloaded VVEL 75 mb")
    except Exception as e:
        print(f"❌ Failed VVEL at {date}: {e}")


C:\Users\adity\AppData\Local\Temp\ipykernel_21060\3543947140.py:5: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  dates = pd.date_range("2020-01-01", "2021-12-31", freq="1H")


⏳ Processing: 2020-01-01 00:00:00
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2020-Jan-01 00:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
👨🏻‍🏭 Created directory: [c:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20200101]
✅ Downloaded VIL
✅ Found ┊ model=hrrr ┊ product=prs ┊ 2020-Jan-01 00:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Downloaded VVEL 75 mb
⏳ Processing: 2020-01-01 01:00:00
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2020-Jan-01 01:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Downloaded VIL
✅ Found ┊ model=hrrr ┊ product=prs ┊ 2020-Jan-01 01:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Downloaded VVEL 75 mb
⏳ Processing: 2020-01-01 02:00:00
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2020-Jan-01 02:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Downloaded VIL
✅ Found ┊ model=hrrr ┊ product=prs ┊ 2020-Jan-01 02:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Downloaded VVEL 75 mb
⏳ Processing: 2020-01-01 03:00:00
✅ Found ┊ model=hrrr ┊ product=sfc ┊ 2020-Jan-01 03:00 UTC F00 ┊ GRIB2 @ aws ┊ IDX @ aws
✅ Download

In [8]:
def crop_data(veril_data):


    target_lat_us_center = 39.8
    target_lon_us_center_neg = -98.5 # Using -180 to 180 convention initially


    if target_lon_us_center_neg < 0:
        target_lon_us_center = 360 + target_lon_us_center_neg # e.g., -98.5W becomes 261.5E
    else:
        target_lon_us_center = target_lon_us_center_neg



    lat_diff_sq = (veril_data.latitude - target_lat_us_center)**2
    lon_diff_sq = (veril_data.longitude - target_lon_us_center)**2


    distance_sq = lat_diff_sq + lon_diff_sq

    # Find the 2D index of the minimum distance
    min_idx_flat = distance_sq.argmin() # This flattens the array and finds the index
    center_y_idx, center_x_idx = np.unravel_index(min_idx_flat.item(), distance_sq.shape)

    center_lat_actual = veril_data.latitude[center_y_idx, center_x_idx].item()
    center_lon_actual = veril_data.longitude[center_y_idx, center_x_idx].item()

    # print(f"Closest grid point to target: y_idx={center_y_idx}, x_idx={center_x_idx}")
    # print(f"  Actual Lat at this point: {center_lat_actual:.3f}")
    # print(f"  Actual Lon at this point: {center_lon_actual:.3f}")

    # 3. Define window size and extract slice
    window_size = 128
    half_window = window_size // 2



    y_start_ideal = center_y_idx - half_window
    x_start_ideal = center_x_idx - half_window


    y_start = np.clip(y_start_ideal, 0, veril_data.shape[0] - window_size)
    x_start = np.clip(x_start_ideal, 0, veril_data.shape[1] - window_size)


    y_end = y_start + window_size
    x_end = x_start + window_size



    # 4. Perform the slice
    veril_subset_us_center = veril_data.isel(y=slice(y_start, y_end), x=slice(x_start, x_end))

    # print(f"\nShape of the subset: {veril_subset_us_center.shape}")
    return(veril_subset_us_center.data)


    # veril_subset_us_center.plot()
    # plt.title(f"128x128 Subset near US Center")
    # plt.show()

# v=crop_data(veril_data)
# v.shape

In [ ]:
from pathlib import Path
import xarray as xr
import  numpy as np

folder_path = Path(r"C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr")


# Iterate through all files in the folder
w_array=[]
vil_array=[]
for file_path in folder_path.iterdir():
    fp=Path(file_path)
    for file_path2 in fp.glob("*.grib2"):
        print(file_path2)
       
        ds = xr.open_dataset(file_path2, engine="cfgrib")
        if "w" in ds.data_vars:
            print("Found variable: w")
            var='w'
            lat=ds.latitude
            lon=ds.longitude

            v_data = ds[var]
            v=crop_data(v_data)
            print("HALO",v.shape)
            w_array.append(v)
        elif "veril" in ds.data_vars:
            print("Found variable: veril")
            var='veril'
            if (lat==ds.latitude).all() and (lon==ds.longitude).all():
                print("paired")
                v_data = ds[var]
                v=crop_data(v_data)
                print("HALO",v.shape)
                w_array.append(v)

            



        

C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_16ef83c9__hrrr.t04z.wrfprsf00.grib2
Found variable: w
HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_16efba75__hrrr.t04z.wrfsfcf00.grib2
Found variable: veril
paired


c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(
c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_2eef83c9__hrrr.t20z.wrfprsf00.grib2
Found variable: w
HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_2eefba75__hrrr.t20z.wrfsfcf00.grib2
Found variable: veril
paired


c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(
c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_34ef83c9__hrrr.t15z.wrfprsf00.grib2
Found variable: w
HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_34efba75__hrrr.t15z.wrfsfcf00.grib2
Found variable: veril
paired


...

HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190104\subset_06ef83c9__hrrr.t08z.wrfprsf00.grib2
Found variable: w
HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190104\subset_06efba75__hrrr.t08z.wrfsfcf00.grib2
Found variable: veril
paired


c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(
c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190104\subset_0fef83c9__hrrr.t03z.wrfprsf00.grib2
Found variable: w
HALO (128, 128)
C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190104\subset_0fefba75__hrrr.t03z.wrfsfcf00.grib2
Found variable: veril
paired


c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(
c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


KeyboardInterrupt: 

In [1]:
import xarray as xr

# Path to your VIL GRIB file (update this to your actual file path)
vil_file = r"C:\Users\adity\OneDrive\Desktop\mscThesis\Code3\Thesis_FLow\bigdata\hrrr\20190101\subset_55efba75__hrrr.t05z.wrfsfcf00.grib2"

# Open the file using xarray with cfgrib engine
ds_vil = xr.open_dataset(vil_file, engine="cfgrib")

print(ds_vil)

<xarray.Dataset> Size: 38MB
Dimensions:     (y: 1059, x: 1799)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    latitude    (y, x) float64 15MB ...
    longitude   (y, x) float64 15MB ...
    valid_time  datetime64[ns] 8B ...
Dimensions without coordinates: y, x
Data variables:
    veril       (y, x) float32 8MB ...
Attributes:
    GRIB_edition:            2
    GRIB_centre:             kwbc
    GRIB_centreDescription:  US National Weather Service - NCEP
    GRIB_subCentre:          0
    Conventions:             CF-1.7
    institution:             US National Weather Service - NCEP
    history:                 2025-06-02T00:54 GRIB to CDM+CF via cfgrib-0.9.1...


c:\Users\adity\anaconda3\envs\tail\Lib\site-packages\cfgrib\xarray_plugin.py:131: FutureWarning: In a future version of xarray decode_timedelta will default to False rather than None. To silence this warning, set decode_timedelta to True, False, or a 'CFTimedeltaCoder' instance.
  vars, attrs, coord_names = xr.conventions.decode_cf_variables(


In [2]:
print(ds_vil.data_vars)

Data variables:
    veril    (y, x) float32 8MB ...


In [3]:
vil_data = ds_vil['veril']
vil_data.shape
# vil_data.plot()
vvel_data=vil_data
print(vvel_data)



<xarray.DataArray 'veril' (y: 1059, x: 1799)> Size: 8MB
[1905141 values with dtype=float32]
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    latitude    (y, x) float64 15MB ...
    longitude   (y, x) float64 15MB ...
    valid_time  datetime64[ns] 8B ...
Dimensions without coordinates: y, x
Attributes: (12/34)
    GRIB_paramId:                             260136
    GRIB_dataType:                            fc
    GRIB_numberOfPoints:                      1905141
    GRIB_typeOfLevel:                         atmosphere
    GRIB_stepUnits:                           1
    GRIB_stepType:                            instant
    ...                                       ...
    GRIB_name:                                Vertically-integrated liquid
    GRIB_shortName:                           veril
    GRIB_units:                               kg m**-1
    long_name:                                Vertically-integrat

In [4]:
veril=vvel_data
lat = veril.latitude
lon = veril.longitude

print(lat.min(),lat.max(),lon.min(),lon.max())

<xarray.DataArray 'latitude' ()> Size: 8B
array(21.138123)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'latitude' ()> Size: 8B
array(52.61565331)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'longitude' ()> Size: 8B
array(225.90452027)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'longitude' ()> Size: 8B
array(299.08280723)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ...


In [ ]:
veril=vvel_data
lat = veril.latitude
lon = veril.longitude

# # Create the mask for your region
# mask = (
#     (lat >= 36.9) & (lat <= 40.18) &
#     (lon >= 265.61) & (lon <= 269.789)
# )





<xarray.DataArray 'latitude' ()> Size: 8B
array(21.138123)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'latitude' ()> Size: 8B
array(52.61565331)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'longitude' ()> Size: 8B
array(225.90452027)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ... <xarray.DataArray 'longitude' ()> Size: 8B
array(299.08280723)
Coordinates:
    time        datetime64[ns] 8B ...
    step        timedelta64[ns] 8B ...
    atmosphere  float64 8B ...
    valid_time  datetime64[ns] 8B ...


(128, 128)

In [213]:
veril.data.shape

(1059, 1799)

In [220]:
print(f"Latitude range: {veril.latitude.min().values} to {veril.latitude.max().values}")
print(f"Longitude range: {veril.longitude.min().values} to {veril.longitude.max().values}")
print(mask.sum())

Latitude range: 21.138123000000004 to 52.6156533068079
Longitude range: 225.90452026573686 to 299.08280722816215
<xarray.DataArray ()> Size: 8B
array(14732)
Coordinates:
    time        datetime64[ns] 8B 2019-01-01T05:00:00
    step        timedelta64[ns] 8B 00:00:00
    atmosphere  float64 8B 0.0
    valid_time  datetime64[ns] 8B 2019-01-01T05:00:00


In [229]:

veril_data=veril

def crop_data(veril_data):


    target_lat_us_center = 39.8
    target_lon_us_center_neg = -98.5 # Using -180 to 180 convention initially


    if target_lon_us_center_neg < 0:
        target_lon_us_center = 360 + target_lon_us_center_neg # e.g., -98.5W becomes 261.5E
    else:
        target_lon_us_center = target_lon_us_center_neg



    lat_diff_sq = (veril_data.latitude - target_lat_us_center)**2
    lon_diff_sq = (veril_data.longitude - target_lon_us_center)**2


    distance_sq = lat_diff_sq + lon_diff_sq

    # Find the 2D index of the minimum distance
    min_idx_flat = distance_sq.argmin() # This flattens the array and finds the index
    center_y_idx, center_x_idx = np.unravel_index(min_idx_flat.item(), distance_sq.shape)

    center_lat_actual = veril_data.latitude[center_y_idx, center_x_idx].item()
    center_lon_actual = veril_data.longitude[center_y_idx, center_x_idx].item()

    # print(f"Closest grid point to target: y_idx={center_y_idx}, x_idx={center_x_idx}")
    # print(f"  Actual Lat at this point: {center_lat_actual:.3f}")
    # print(f"  Actual Lon at this point: {center_lon_actual:.3f}")

    # 3. Define window size and extract slice
    window_size = 128
    half_window = window_size // 2



    y_start_ideal = center_y_idx - half_window
    x_start_ideal = center_x_idx - half_window


    y_start = np.clip(y_start_ideal, 0, veril_data.shape[0] - window_size)
    x_start = np.clip(x_start_ideal, 0, veril_data.shape[1] - window_size)


    y_end = y_start + window_size
    x_end = x_start + window_size



    # 4. Perform the slice
    veril_subset_us_center = veril_data.isel(y=slice(y_start, y_end), x=slice(x_start, x_end))

    # print(f"\nShape of the subset: {veril_subset_us_center.shape}")
    return(veril_subset_us_center.data)


    # veril_subset_us_center.plot()
    # plt.title(f"128x128 Subset near US Center")
    # plt.show()

v=crop_data(veril_data)
v.shape

(128, 128)

array([[0.00032, 0.00016, 0.00048, ..., 0.00032, 0.00032, 0.00016],
       [0.00016, 0.00032, 0.00032, ..., 0.00048, 0.00048, 0.00032],
       [0.00016, 0.00016, 0.00032, ..., 0.00048, 0.00048, 0.00048],
       ...,
       [0.     , 0.     , 0.     , ..., 0.00016, 0.00016, 0.00016],
       [0.     , 0.     , 0.     , ..., 0.00016, 0.00016, 0.00016],
       [0.     , 0.     , 0.     , ..., 0.00016, 0.00064, 0.00064]],
      shape=(128, 128), dtype=float32)